In [4]:
import pandas as pd

data = pd.read_csv("Restaurant reviews.csv")
data

Restaurant              Reviewer  \
0      Beyond Flavours     Rusha Chakraborty   
1      Beyond Flavours  Anusha Tirumalaneedi   
2      Beyond Flavours       Ashok Shekhawat   
3      Beyond Flavours        Swapnil Sarkar   
4      Beyond Flavours                Dileep   
...                ...                   ...   
9995  Chinese Pavilion      Abhishek Mahajan   
9996  Chinese Pavilion        Sharad Agrawal   
9997  Chinese Pavilion             Ramandeep   
9998  Chinese Pavilion       Nayana Shanbhag   
9999  Chinese Pavilion      Bhargava Krishna   

                                                 Review Rating  \
0     The ambience was good, food was quite good . h...      5   
1     Ambience is too good for a pleasant evening. S...      5   
2     A must try.. great food great ambience. Thnx f...      5   
3     Soumen das and Arun was a great guy. Only beca...      5   
4     Food is good.we ordered Kodi drumsticks and ba...      5   
...                                                 ...    ...   
9995  Madhumathi Mahajan Well to start with nice cou...      3   
9996  This place has never disappointed us.. The foo...    4.5   
9997  Bad rating is mainly because of "Chicken Bone ...    1.5   
9998  I personally love and prefer Chinese Food. Had...      4   
9999  Checked in here to try some delicious chinese ...    3.5   

                          Metadata             Time Pictures  
0           1 Review , 2 Followers  5/25/2019 15:54        0  
1          3 Reviews , 2 Followers  5/25/2019 14:20        0  
2          2 Reviews , 3 Followers  5/24/2019 22:54        0  
3            1 Review , 1 Follower  5/24/2019 22:11        0  
4          3 Reviews , 2 Followers  5/24/2019 21:37        0  
...                            ...              ...      ...  
9995     53 Reviews , 54 Followers    6/5/2016 0:08        0  
9996      2 Reviews , 53 Followers   6/4/2016 22:01        0  
9997    65 Reviews , 423 Followers   6/3/2016 10:37        3  
9998    13 Reviews , 144 Followers  5/31/2016 17:22        0  
9999  472 Reviews , 1302 Followers  5/31/2016 16:41        6  

[10000 rows x 7 columns]

In [5]:
review_data = data.drop(['Reviewer', 'Rating', 'Metadata', 'Time', 'Pictures'], axis=1) 
review_data['Review'] = review_data['Review'].astype(str)

# Data cleaning and making data set according to the requirements
#combined_data = review_data.groupby(['Restaurant'])['Review'].apply(list).reset_index()
combined_data = review_data.groupby('Restaurant').agg({'Review': ' .'.join}).reset_index()

dict_data = combined_data.to_dict('records')
dict_data

[{'Restaurant': '10 Downing Street',
  'Review': 'I\'ve been to this place about two times and i really liked the ambience, interior will give you feels of london streets.\ntalking about food, only good thing was lasagna other than that we ordered veg Platter and lasagna rolls which were really bad in taste. dj was not too good .I have visited this pub last weekend with group of friends, we had brewed beers, veg & non-veg starters. Food tastes good, prices are reasonable, ambience is decent, service is good even though it’s on Saturday night.\n\nOverall i liked the place, I will visit again!! .Surely one of the best lasagna you can have. The place never disappoints you even when you are just trying something for the first time here. Chilli cheese toast is something you have to try .\n\nGreat food at budget price with good service in a lovely ambience.\nWhat more can you ask for.... .Closed ambiance, loud. Food was filling, we ordered veg platter and the pizza is a must try, thin crust 

In [6]:
import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /home/rajatk/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


True

In [7]:
def analyze_sentiment(review_text):
    sia = SentimentIntensityAnalyzer()
    sentiment_scores = sia.polarity_scores(review_text)
    # print(sentiment_scores)
    sentiment = "Positive" if sentiment_scores['compound'] > 0 else "Negative"
    return sentiment

for i, review_statement in enumerate(dict_data):
    #print(i, review_statement)
    sentiment = analyze_sentiment(review_statement['Review'])
    dict_data[i].update({'Sentiment': f'{sentiment}'})

dict_data

[{'Restaurant': '10 Downing Street',
  'Review': 'I\'ve been to this place about two times and i really liked the ambience, interior will give you feels of london streets.\ntalking about food, only good thing was lasagna other than that we ordered veg Platter and lasagna rolls which were really bad in taste. dj was not too good .I have visited this pub last weekend with group of friends, we had brewed beers, veg & non-veg starters. Food tastes good, prices are reasonable, ambience is decent, service is good even though it’s on Saturday night.\n\nOverall i liked the place, I will visit again!! .Surely one of the best lasagna you can have. The place never disappoints you even when you are just trying something for the first time here. Chilli cheese toast is something you have to try .\n\nGreat food at budget price with good service in a lovely ambience.\nWhat more can you ask for.... .Closed ambiance, loud. Food was filling, we ordered veg platter and the pizza is a must try, thin crust 

In [8]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel

# TF-IDF vectorizer
tfidf_vectorizer = TfidfVectorizer(stop_words='english')

# TF-IDF matrix
tfidf_matrix = tfidf_vectorizer.fit_transform([restaurant['Review'] for restaurant in dict_data])

cosine_sim = linear_kernel(tfidf_matrix, tfidf_matrix)

# Function to get restaurant recommendations
def get_recommendations(name, cosine_sim=cosine_sim):
    idx = next((i for i, restaurant in enumerate(dict_data) if restaurant['Restaurant'] == name), None)
    if idx is None:
        return []

    sim_scores = list(enumerate(cosine_sim[idx]))
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
    sim_scores = sim_scores[1:6]  # Get top 5 similar restaurants
    restaurant_indices = [i[0] for i in sim_scores]

    return [(dict_data[i]['Restaurant'], dict_data[i]['Sentiment'] +" Reviews") for i in restaurant_indices]

In [10]:
# Use restaurant name from the initial data set
restaurant_name = "American Wild Wings" # Example restaurant name taken from the dataset
recommended_restaurants = get_recommendations(restaurant_name)
print(f"Recommended Restaurants for {restaurant_name}: {recommended_restaurants}")

Recommended Restaurants for American Wild Wings: [('Deli 9 Bistro', 'Positive Reviews'), ('Olive Garden', 'Positive Reviews'), ('Biryanis And More', 'Positive Reviews'), ('Being Hungry', 'Positive Reviews'), ('B-Dubs', 'Positive Reviews')]
